# debug

In [1]:
import torch

import tvm
from tvm import tir
from tvm.relax.frontend import nn
from tvm.relax.frontend.nn import op, spec
from tvm.runtime import NDArray

## `print`

In [2]:
class Layer(nn.Module):
    def forward(self, x: nn.Tensor):  # pylint: disable=invalid-name
        op.print_(x)
        return x

model = Layer().jit(
    spec={
        "forward": {"x": spec.Tensor([10, 5], dtype="float32")},
    },
    debug=True,
)
x = torch.rand((10, 5), dtype=torch.float32)  # pylint: disable=invalid-name
y = model["forward"](x)  # pylint: disable=invalid-name
assert isinstance(y, torch.Tensor)


/tmp/ipykernel_1225526/3381093976.py:3: shape = (10, 5), dtype = float32, data =
[[0.73462075 0.01047635 0.31426018 0.8674046  0.12726694]
 [0.05869561 0.14252067 0.57591957 0.62454313 0.5909737 ]
 [0.04823518 0.8938983  0.89632434 0.15392512 0.18556875]
 [0.31064558 0.6404101  0.62769175 0.1271398  0.89232284]
 [0.16888297 0.4059453  0.70379585 0.77904415 0.84397256]
 [0.00197196 0.48467797 0.3471346  0.00262749 0.82645226]
 [0.28290933 0.51377964 0.67835134 0.04419875 0.07198626]
 [0.00947952 0.96474004 0.16065902 0.33178765 0.49370688]
 [0.6731469  0.5020207  0.44368893 0.4925446  0.45231378]
 [0.48918706 0.0983749  0.9165322  0.5107241  0.788272  ]]


## 调试函数

In [4]:
@tvm.register_func("testing.relax.frontend.nn.test_debug_func")
def _debug(  # pylint: disable=too-many-arguments
    lineno: str,
    tensor: NDArray,
    const_int: int,
    const_float: float,
    const_str: str,
    var_int: int,
) -> None:
    assert "test_frontend_nn_debug.py" in lineno
    assert tensor.shape == (10, 5)
    assert const_int == 1
    assert const_float == 2.0
    assert const_str == "test"
    assert var_int == 8

class Layer(nn.Module):
    def forward(self, x: nn.Tensor, v: tir.Var):  # pylint: disable=invalid-name
        op.debug_func("testing.relax.frontend.nn.test_debug_func", x, 1, 2.0, "test", v)
        return x

model = Layer().jit(
    spec={
        "forward": {
            "x": spec.Tensor([10, 5], dtype="float32"),
            "v": "int",
        },
    },
    debug=True,
)
x = torch.rand((10, 5), dtype=torch.float32)  # pylint: disable=invalid-name
y = model["forward"](x, 8)  # pylint: disable=invalid-name
assert isinstance(y, torch.Tensor)

AssertionError: 